<a href="https://colab.research.google.com/github/KyleHung7/programming-language/blob/main/Week_9_Advanced_2019_2023_Financial_Report_Analysis_Gemini_Text.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **2019-2023 上市公司財報分析**

In [1]:
from google.colab import auth
auth.authenticate_user()

import gspread
from google.auth import default
creds, _ = default()

gc = gspread.authorize(creds)

In [2]:
import pandas as pd
# read data and put it in a dataframe
# 在 google 工作表載入 gsheets
gsheets = gc.open_by_url('https://docs.google.com/spreadsheets/d/1ILPJ0bUYlHAmfeFzk_kZ3rs2X13lGLAd-ikADZpC1_w/edit?usp=sharing')

In [3]:
from gspread_dataframe import set_with_dataframe

# 選擇要更新的工作表（選擇第一個工作表）
worksheet_gemini = gsheets.get_worksheet(11)


In [4]:
# 取得 Google Sheets 內容
data_gemini = worksheet_gemini.get_all_values()  # 取得所有儲存格資料，回傳為 2D 陣列


# 將資料轉換為 DataFrame
df_gemini = pd.DataFrame(data_gemini)



In [5]:
df_gemini.head()

0
0                                         Gemini財報分析
1  好的，我已經準備好分析這些財報數據了。由於篇幅限制，我會盡量簡潔地呈現我的分析結果。\n\n...
2  19、3,538、3,294、未提供\n**1225、福懋油**、11,244、10,647...
3  提供\n**1314、中石化**、38,503、29,624、17,583、35,163、2...
4  304、台聚**: 61,797\n**1305、華夏**: 15,430\n**1307、...

#### 5.文字訊息分析

In [6]:
!pip install jieba
!pip install snownlp

In [7]:
!apt-get update -qq
!apt-get install -y fonts-wqy-zenhei

W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InRelease' does not seem to provide it (sources.list entry misspelt?)
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
fonts-wqy-zenhei is already the newest version (0.9.45-8).
0 upgraded, 0 newly installed, 0 to remove and 36 not upgraded.


In [18]:
import re
import pandas as pd
import jieba
from snownlp import SnowNLP
from collections import Counter
import plotly.express as px

# 自訂函數：提取中文字
def extract_chinese(text):
    if not isinstance(text, str):
        return ""
    return ''.join(re.findall(r'[\u4e00-\u9fff]+', text))

# 定義表格解析函數
def parse_score_table(content):
    # 匹配表格行，格式如：1101 | 台泥 | 4 | 4 | 4 | 12
    score_pattern = r'(\d+)\s*\|\s*([\u4e00-\u9fff]+)\s*\|\s*(\d+)\s*\|\s*(\d+)\s*\|\s*(\d+)\s*\|\s*(\d+)'
    matches = re.findall(score_pattern, content)
    result = []
    for match in matches:
        company_code, company_name, revenue_growth, profitability, stability, total = match
        result.append({
            '公司代碼': company_code,
            '公司名稱': company_name,
            '營收成長評分': int(revenue_growth),
            '獲利能力評分': int(profitability),
            '財務穩健性評分': int(stability),
            '總分': int(total),
            '年度': '2019-2023'
        })
    return result

# 定義表現等級函數
def determine_performance(total_score):
    if total_score >= 14:
        return '優異'
    elif total_score >= 11:
        return '良好'
    elif total_score >= 8:
        return '中性'
    elif total_score >= 5:
        return '一般'
    else:
        return '較差'

# 主程式
# 將第一列設為欄位名稱，其餘為資料內容
df_gemini = pd.DataFrame(data_gemini[1:], columns=data_gemini[0])

# 檢查 'Gemini財報分析' 欄位是否存在
if 'Gemini財報分析' not in df_gemini.columns:
    print("⚠️ 'Gemini財報分析' 欄位不存在，請確認你的 Google Sheets 欄位名稱")
    exit()

# 將 'Gemini財報分析' 中的詞加入 Jieba 詞典
for word in df_gemini['Gemini財報分析']:
    jieba.add_word(word, freq=10000)
    jieba.suggest_freq(word, tune=True)

# 清理與斷詞
df_gemini['Cleaned_Gemini財報分析'] = df_gemini['Gemini財報分析'].apply(lambda x: str(x).strip())
df_gemini['Chinese_Gemini財報分析'] = df_gemini['Cleaned_Gemini財報分析'].apply(extract_chinese)
df_gemini['Tokenized'] = df_gemini['Chinese_Gemini財報分析'].apply(lambda x: list(jieba.cut(x, HMM=True)))

# 展平成所有詞語（長度 > 1 的字）
all_words = [word for tokens in df_gemini['Tokenized'] for word in tokens if len(word) > 1]


In [19]:
df_gemini['Tokenized']

0      [好, 的, 我, 已經, 準備, 好, 分析, 這些, 財報, 數據, 了, 由, 於, ...
1      [未, 提供, 福懋油, 未, 提供, 佳格, 未, 提供, 聯華未, 提供, 聯華食, 未...
2      [提供, 中石化, 未, 提供, 達, 新, 未, 提供, 上曜, 未, 提供, 東陽, 未...
3      [台聚華夏, 三芳亞, 聚台, 達化, 台苯國, 喬聯成, 中石化, 達新上, 曜, 東陽,...
4      [味全, 味王, 大成, 大飲卜, 蜂統, 一愛之味, 泰山, 福壽台, 榮福懋油佳格, 聯...
                             ...                        
112    [運動, 休閒, 營收, 獲利, 下滑, 櫻花, 居家, 生活, 營收, 獲利, 穩定, 成...
113    [新海, 營收, 平穩, 獲利, 尚可, 泰銘營, 收, 下滑, 獲利, 尚可, 財務極, ...
114    [營收, 平穩, 獲利, 尚可, 百和營, 收, 獲利, 下滑, 宏全, 營收, 獲利, 穩...
115    [佳龍, 綠能, 環保營, 收, 下滑, 持續, 虧, 損世紀, 鋼營, 收成, 長, 獲利...
116    [業旺, 豐祥, 億豐, 櫻花表現, 突出, 拓凱, 復, 盛應, 用鈺齊, 豐泰, 雖屬,...
Name: Tokenized, Length: 117, dtype: object

In [20]:
# 解析所有報告的表格
all_scores = []
for idx, row in df_gemini.iterrows():
    scores = parse_score_table(row['Cleaned_Gemini財報分析'])
    for score in scores:
        score['報告索引'] = idx  # 記錄來源報告
        all_scores.append(score)

# 轉為 DataFrame
if all_scores:
    summary = pd.DataFrame(all_scores)
else:
    summary = pd.DataFrame(columns=['公司代碼', '公司名稱', '年度', '營收成長評分', '獲利能力評分', '財務穩健性評分', '總分', '報告索引'])

# 若無數據，提前退出
if summary.empty:
    print("⚠️ 無法從報告中提取評分數據，請檢查 'Gemini財報分析' 內容")
    exit()

# 判斷表現等級
summary['表現等級'] = summary['總分'].apply(determine_performance)

# 計算每家公司的平均評分
company_scores = summary.groupby('公司名稱').agg({
    '營收成長評分': 'mean',
    '獲利能力評分': 'mean',
    '財務穩健性評分': 'mean',
    '總分': 'mean'
}).reset_index()
company_scores['表現等級'] = company_scores['總分'].apply(determine_performance)
company_scores = company_scores.sort_values('總分', ascending=False)

# 找出最佳公司
best_company = company_scores.iloc[0]['公司名稱'] if not company_scores.empty else '無有效數據'

# 輸出結果
print("財報分析評分表：")
print(summary[['公司名稱', '年度', '營收成長評分', '獲利能力評分', '財務穩健性評分', '總分', '表現等級']].to_string(index=False))
print("\n公司平均評分表：")
print(company_scores[['公司名稱', '營收成長評分', '獲利能力評分', '財務穩健性評分', '總分', '表現等級']].to_string(index=False))
print(f"\n結論：表現最優異的公司是 {best_company}，平均總分為 {company_scores.iloc[0]['總分']:.2f} 分。" if not company_scores.empty else "\n結論：無有效數據可分析。")


財報分析評分表：
 公司名稱        年度  營收成長評分  獲利能力評分  財務穩健性評分  總分 表現等級
   台泥 2019-2023       4       4        4  12   良好
   亞泥 2019-2023       3       3        4  10   中性
   嘉泥 2019-2023       1       1        1   3   較差
   環泥 2019-2023       3       3        3   9   中性
   幸福 2019-2023       2       2        2   6   一般
   信大 2019-2023       2       2        2   6   一般
   味全 2019-2023       3       3        3   9   中性
   味王 2019-2023       2       2        2   6   一般
   大成 2019-2023       4       4        4  12   良好
   大飲 2019-2023       1       1        1   3   較差
   卜蜂 2019-2023       3       3        3   9   中性
   統一 2019-2023       5       5        5  15   優異
  愛之味 2019-2023       2       2        2   6   一般
   泰山 2019-2023       2       2        2   6   一般
   福壽 2019-2023       3       3        3   9   中性
   台榮 2019-2023       2       2        2   6   一般
  福懋油 2019-2023       3       3        3   9   中性
   佳格 2019-2023       3       3        3   9   中性
   聯華 2019-2023       3       3        3 

In [21]:
import re
import pandas as pd
import jieba
from snownlp import SnowNLP
from collections import Counter
import plotly.express as px
from wordcloud import WordCloud
import matplotlib.pyplot as plt
import numpy as np
import os
import platform

# 自訂函數：提取中文字
def extract_chinese(text):
    if not isinstance(text, str):
        return ""
    return ''.join(re.findall(r'[\u4e00-\u9fff]+', text))

# 定義三種斷詞模式（僅全模式與搜尋模式）
def tokenize_modes(text):
    return {
        '全模式': list(jieba.cut(text, cut_all=True)),
        '搜尋模式': list(jieba.cut_for_search(text))
    }

# 生成文字雲函數（修復字型問題）
def generate_wordcloud(freq_df, title):
    try:
        # 根據作業系統選擇字型
        system = platform.system()
        font_path = None
        possible_fonts = [
            # Linux 常用字型
            '/usr/share/fonts/truetype/wqy/wqy-zenhei.ttc',  # 文泉驛正黑
            '/usr/share/fonts/opentype/noto/NotoSansCJK-Regular.ttc',  # Noto Sans CJK
            # Windows 常用字型
            'C:/Windows/Fonts/msyh.ttc',  # 微軟雅黑
            'C:/Windows/Fonts/simsun.ttc',  # 新宋體
            # macOS 常用字型
            '/System/Library/Fonts/PingFang.ttc',  # 蘋方
            '/Library/Fonts/NotoSansCJKsc-Regular.otf',  # Noto Sans CJK
        ]

        # 檢查字型檔案是否存在
        for path in possible_fonts:
            if os.path.exists(path):
                font_path = path
                break

        # 如果未找到字型，提示使用者
        if font_path is None:
            raise FileNotFoundError("未找到可用的中文字型檔案，請安裝 Noto Sans CJK 或其他中文字型")

        # 生成文字雲
        wordcloud = WordCloud(
            width=800,
            height=400,
            background_color='white',
            font_path=font_path
        )
        wordcloud.generate_from_frequencies(dict(zip(freq_df['詞語'], freq_df['頻率'])))
        plt.figure(figsize=(10, 5))
        plt.imshow(wordcloud, interpolation='bilinear')
        plt.axis('off')
        plt.title(title)
        plt.show()
    except Exception as e:
        print(f"⚠️ 無法生成文字雲：{e}")
        print("請確認已安裝中文字型（如 Noto Sans CJK），或檢查字型路徑設定")

# 定義表格解析函數
def parse_score_table(content):
    score_pattern = r'(\d+)\s*\|\s*([\u4e00-\u9fff]+)\s*\|\s*(\d+)\s*\|\s*(\d+)\s*\|\s*(\d+)\s*\|\s*(\d+)'
    matches = re.findall(score_pattern, content)
    result = []
    for match in matches:
        company_code, company_name, revenue_growth, profitability, stability, total = match
        result.append({
            '公司代碼': company_code,
            '公司名稱': company_name,
            '營收成長評分': int(revenue_growth),
            '獲利能力評分': int(profitability),
            '財務穩健性評分': int(stability),
            '總分': int(total),
            '年度': '2019-2023'
        })
    return result

# 定義表現等級函數
def determine_performance(total_score):
    if total_score >= 14:
        return '優異'
    elif total_score >= 11:
        return '良好'
    elif total_score >= 8:
        return '中性'
    elif total_score >= 5:
        return '一般'
    else:
        return '較差'

# 定義評分分類函數
def classify_score(score):
    if score >= 4:
        return '高'
    elif score == 3:
        return '中'
    else:
        return '低'

# 定義詞頻統計與可視化函數
def analyze_freq(mode, freq_df, title_prefix, x_label):
    # 條形圖
    sorted_df = freq_df.head(30).sort_values(by='頻率', ascending=False)
    fig_bar = px.bar(
        sorted_df,
        x='詞語',
        y='頻率',
        title=f'{title_prefix}（{mode} 前 30 名）',
        labels={'詞語': x_label, '頻率': '出現次數'},
        text='頻率'
    )
    fig_bar.update_traces(texttemplate='%{text}', textposition='outside')
    fig_bar.update_layout(
        template='plotly_white',
        xaxis=dict(title=x_label),
        yaxis=dict(title='出現次數')
    )
    fig_bar.show()

    # 文字雲
    top_words = freq_df.head(300)
    try:
        # 動態選擇字型
        system = platform.system()
        font_path = None
        possible_fonts = [
            '/usr/share/fonts/truetype/wqy/wqy-zenhei.ttc',
            '/usr/share/fonts/opentype/noto/NotoSansCJK-Regular.ttc',
            'C:/Windows/Fonts/msyh.ttc',
            'C:/Windows/Fonts/simsun.ttc',
            '/System/Library/Fonts/PingFang.ttc',
            '/Library/Fonts/NotoSansCJKsc-Regular.otf',
        ]
        for path in possible_fonts:
            if os.path.exists(path):
                font_path = path
                break
        if font_path is None:
            raise FileNotFoundError("未找到可用的中文字型檔案，請安裝 Noto Sans CJK 或其他中文字型")

        wordcloud = WordCloud(
            width=800,
            height=400,
            background_color='white',
            font_path=font_path
        )
        wordcloud.generate_from_frequencies(dict(zip(top_words['詞語'], top_words['頻率'])))
        wordcloud_img = wordcloud.to_array()
        fig_wc = px.imshow(wordcloud_img)
        fig_wc.update_layout(
            title=f'文字雲（{mode}）',
            xaxis=dict(showgrid=False, showticklabels=False, zeroline=False),
            yaxis=dict(showgrid=False, showticklabels=False, zeroline=False),
            coloraxis_showscale=False
        )
        fig_wc.show()
    except Exception as e:
        print(f"⚠️ 文字雲生成失敗（{mode}），請確認 wordcloud 套件與字體路徑：{e}")

# 主程式
# 假設 data_gemini 是從 Google Sheet 載入的數據
# data_gemini = [...]  # 請自行載入資料
df_gemini = pd.DataFrame(data_gemini[1:], columns=data_gemini[0])

# 檢查 'Gemini財報分析' 欄位是否存在
if 'Gemini財報分析' not in df_gemini.columns:
    print("⚠️ 'Gemini財報分析' 欄位不存在，請確認你的 Google Sheets 欄位名稱")
    exit()

# 將 'Gemini財報分析' 中的詞加入 Jieba 詞典
for word in df_gemini['Gemini財報分析']:
    jieba.add_word(word, freq=10000)
    jieba.suggest_freq(word, tune=True)

# 清理與斷詞
df_gemini['Cleaned_Gemini財報分析'] = df_gemini['Gemini財報分析'].apply(lambda x: str(x).strip())
df_gemini['Chinese_Gemini財報分析'] = df_gemini['Cleaned_Gemini財報分析'].apply(extract_chinese)
df_gemini['Tokenized'] = df_gemini['Chinese_Gemini財報分析'].apply(lambda x: list(jieba.cut(x, HMM=True)))

# 解析所有報告的表格
all_scores = []
for idx, row in df_gemini.iterrows():
    scores = parse_score_table(row['Cleaned_Gemini財報分析'])
    for score in scores:
        score['報告索引'] = idx
        all_scores.append(score)

# 轉為 DataFrame
if all_scores:
    summary = pd.DataFrame(all_scores)
else:
    summary = pd.DataFrame(columns=['公司代碼', '公司名稱', '年度', '營收成長評分', '獲利能力評分', '財務穩健性評分', '總分', '報告索引'])

# 若無數據，提前退出
if summary.empty:
    print("⚠️ 無法從報告中提取評分數據，請檢查 'Gemini財報分析' 內容")
    exit()

# 判斷表現等級
summary['表現等級'] = summary['總分'].apply(determine_performance)

# 分類公司表現（高、中、低）
summary['營收成長等級'] = summary['營收成長評分'].apply(classify_score)
summary['獲利能力等級'] = summary['獲利能力評分'].apply(classify_score)
summary['財務穩健性等級'] = summary['財務穩健性評分'].apply(classify_score)

# 按維度匯總公司
for dimension, column in [
    ('營收成長', '營收成長等級'),
    ('獲利能力', '獲利能力等級'),
    ('財務穩健性', '財務穩健性等級')
]:
    print(f"\n{dimension}表現分類：")
    for level in ['高', '中', '低']:
        companies = summary[summary[column] == level]['公司名稱'].unique().tolist()
        print(f"{level}：{', '.join(companies) if companies else '無'}")

# 計算每家公司的平均評分
company_scores = summary.groupby('公司名稱').agg({
    '營收成長評分': 'mean',
    '獲利能力評分': 'mean',
    '財務穩健性評分': 'mean',
    '總分': 'mean'
}).reset_index()
company_scores['表現等級'] = company_scores['總分'].apply(determine_performance)
company_scores = company_scores.sort_values('總分', ascending=False)

# 儲存公司平均評分到 CSV
company_scores.to_csv('company_scores.csv', index=False, encoding='utf-8-sig')
print("\n公司平均評分已儲存至 'company_scores.csv'")

# 找出最佳公司
best_company = company_scores.iloc[0]['公司名稱'] if not company_scores.empty else '無有效數據'

# 按表現等級進行詞頻分析並儲存 CSV
performance_levels = ['優異', '良好', '中性', '一般', '較差']
company_names = summary['公司名稱'].unique().tolist()

for level in performance_levels:
    print(f"\n=== 表現等級：{level} ===")

    # 篩選該等級的報告索引
    level_indices = summary[summary['表現等級'] == level]['報告索引'].unique()
    level_texts = df_gemini.loc[df_gemini.index.isin(level_indices), 'Chinese_Gemini財報分析']
    level_tokenized = df_gemini.loc[df_gemini.index.isin(level_indices), 'Tokenized']

    if level_texts.empty:
        print(f"無 {level} 等級的報告數據")
        continue

    # 公司詞頻
    company_freq = Counter()
    for text in level_texts:
        for company in company_names:
            company_freq[company] += text.count(company)
    company_freq_df = pd.DataFrame(company_freq.items(), columns=['詞語', '頻率'])
    company_freq_df = company_freq_df.sort_values(by='頻率', ascending=False).reset_index(drop=True)

    # 輸出公司詞頻
    print(f"\n公司詞頻統計表（{level}，前 50 名）：")
    print(company_freq_df.head(50).to_string(index=False))

    # 儲存公司詞頻到 CSV
    company_freq_csv = f'company_freq_{level}.csv'
    company_freq_df.to_csv(company_freq_csv, index=False, encoding='utf-8-sig')
    print(f"公司詞頻已儲存至 '{company_freq_csv}'")

    analyze_freq(f'{level} 公司詞頻', company_freq_df, f'公司出現次數統計 - {level}', '公司名稱')

    # 內容詞頻（三種斷詞模式）
    mode_word_freq = {}

    # 精確模式：使用 Tokenized
    all_words_precision = [word for tokens in level_tokenized for word in tokens if len(word) > 1]
    counter_precision = Counter(all_words_precision)
    word_freq_precision = pd.DataFrame(counter_precision.items(), columns=['詞語', '頻率'])
    word_freq_precision = word_freq_precision.sort_values(by='頻率', ascending=False).reset_index(drop=True)
    mode_word_freq['精確模式'] = word_freq_precision

    # 全模式與搜尋模式：對合併文字重新斷詞
    combined_text = ' '.join(level_texts)
    for mode, tokens in tokenize_modes(combined_text).items():
        filtered = [word for word in tokens if len(word) > 1]
        counter = Counter(filtered)
        word_freq_df = pd.DataFrame(counter.items(), columns=['詞語', '頻率'])
        word_freq_df = word_freq_df.sort_values(by='頻率', ascending=False).reset_index(drop=True)
        mode_word_freq[mode] = word_freq_df

    # 輸出與可視化內容詞頻
    for mode in ['精確模式', '全模式', '搜尋模式']:
        print(f"\n內容詞頻統計表（{level} - {mode}，前 50 名）：")
        print(mode_word_freq[mode].head(50).to_string(index=False))

        # 儲存內容詞頻到 CSV
        word_freq_csv = f'word_freq_{level}_{mode}.csv'
        mode_word_freq[mode].to_csv(word_freq_csv, index=False, encoding='utf-8-sig')
        print(f"內容詞頻（{mode}）已儲存至 '{word_freq_csv}'")

        analyze_freq(f'{level} - {mode}', mode_word_freq[mode], f'內容關鍵字出現次數統計 - {level}', '關鍵字')


營收成長表現分類：
高：台泥, 大成, 統一, 台塑, 南亞, 聯成, 卜蜂, 聯華, 聯華食, 東陽, 勤益控, 三洋實業, 業旺, 儒鴻, 聚陽, 士電, 中興電, 亞力, 華城, 樂事綠能, 華電, 大山, 合機, 葡萄王, 生達, 喬山, 南光, 和康生, 科妍, 美時, 東和鋼鐵, 新光鋼, 川湖, 三陽工業, 和泰車, 長榮鋼, 汎德永業, 聯電, 台達電, 華通, 台積電, 海悅, 微星, 瑞昱, 廣達, 台光電, 群光, 威盛, 研華, 漢唐, 中華電, 精技, 固緯, 新美齊, 凌群, 聯發科, 資通, 鉅祥, 敦陽科, 國產, 龍邦, 皇普, 愛山林, 皇昌, 根基, 長榮, 榮運, 漢翔, 長榮航太, 八方雲集, 台中銀, 台產, 臺企銀, 新產, 中再保, 第一保, 玉山金, 台新金, 永豐金, 王道銀行, 統一超, 三商家購, 神基, 華立, 奇鋐, 信邦, 零壹, 智原, 文曄, 欣興, 健鼎, 台灣大, 一零四, 耀登, 弘憶股, 玉晶光, 創意, 安馳, 嘉澤, 辛耘, 智易, 健策, 大眾控, 日月光投控, 定穎投控, 佳醫, 承業醫, 南寶, 遠傳, 十銓, 全訊, 虹堡, 祥碩, 中磊, 崇越, 亞翔, 關貿, 帆宣, 佳必琪, 精誠, 啟碁, 樺漢, 迅得, 保瑞, 晶碩, 晶心科, 和潤企業, 帝寶, 必應, 洋基工程, 龍德造船, 晉弘, 森崴能源, 勤誠, 富邦媒, 潤泰材, 東哥遊艇, 高力, 欣巴巴, 櫻花, 中保科, 中鼎, 宏全, 裕融, 世紀鋼
中：亞泥, 環泥, 味全, 卜蜂, 福壽, 福懋油, 佳格, 聯華, 聯華食, 大統益, 黑松, 三芳, 東陽, 永裕, 愛之味, 泰山, 遠東新, 名軒, 東元, 永大, 耿鼎, 江申, 中宇, 中砂, 倉佑, 信錦, 吉茂, 聲寶, 宏泰, 三洋電, 億泰, 中化, 南僑, 興農, 台肥, 永記, 美吾華, 杏輝, 臺鹽, 中化生, 勝一, 潤隆, 凱撒衛, 台紙, 正隆, 中鋼構, 豐興, 美亞, 建大, 中華, 劍麟, 宇隆, 麗正, 鴻海, 仁寶, 廣宇, 光罩, 聯強, 佳世達, 英業達, 華碩, 所羅門, 致茂, 技嘉, 精元, 正崴, 毅嘉, 建準, 三商電, 興勤, 偉詮電, 超豐, 全新, 義隆, 華經, 強茂, 揚博, 中工, 冠德, 達欣工, 


內容詞頻統計表（優異 - 精確模式，前 50 名）：
    詞語  頻率
    味全   1
    味王   1
    大成   1
   大飲卜   1
    蜂統   1
  一愛之味   1
    泰山   1
   福壽台   1
榮福懋油佳格   1
    聯華   1
   聯華食   1
   大統益   1
    天仁   1
    黑松   1
  興泰宏亞   1
    鮮活   1
    果汁   1
    台塑   1
   南亞台   1
   聚華夏   1
   三芳亞   1
    聚台   1
    達化   1
   台苯國   1
   喬聯成   1
   中石化   1
   達新上   1
內容詞頻（精確模式）已儲存至 'word_freq_優異_精確模式.csv'



內容詞頻統計表（優異 - 全模式，前 50 名）：
 詞語  頻率
 味全   1
 大成   1
 成大   1
 泰山   1
 黑松   1
 果汁   1
 台塑   1
 中石   1
中石化   1
 石化   1
內容詞頻（全模式）已儲存至 'word_freq_優異_全模式.csv'



內容詞頻統計表（優異 - 搜尋模式，前 50 名）：
    詞語  頻率
    味全   1
    味王   1
    大成   1
   大飲卜   1
    蜂統   1
  一愛之味   1
    泰山   1
   福壽台   1
榮福懋油佳格   1
    聯華   1
   聯華食   1
   大統益   1
    天仁   1
    黑松   1
  興泰宏亞   1
    鮮活   1
    果汁   1
    台塑   1
   南亞台   1
   聚華夏   1
   三芳亞   1
    聚台   1
    達化   1
   台苯國   1
   喬聯成   1
    中石   1
    石化   1
   中石化   1
   達新上   1
內容詞頻（搜尋模式）已儲存至 'word_freq_優異_搜尋模式.csv'



=== 表現等級：良好 ===

公司詞頻統計表（良好，前 50 名）：
 詞語  頻率
 南亞   4
 聯成   4
 統一   4
 台塑   4
 大成   3
 台聚   2
 福懋   2
 華夏   2
 三芳   2
 聯華   2
 佳格   2
 亞泥   2
 亞聚   2
台達化   2
 台苯   2
 卜蜂   2
中石化   2
 味全   2
 達新   2
福懋油   2
 上曜   2
 國喬   2
 東陽   1
 大洋   1
 東泥   1
 台泥   1
 嘉泥   1
 環泥   1
 幸福   1
 信大   1
 味王   1
 大飲   1
愛之味   1
 泰山   1
 福壽   1
 台榮   1
聯華食   1
大統益   1
 黑松   1
 興泰   1
 天仁   1
 宏亞   1
 智易   0
 谷崧   0
 洋華   0
 宏致   0
 瑞鼎   0
艾笛森   0
 通嘉   0
 辛耘   0
公司詞頻已儲存至 'company_freq_良好.csv'


...


內容詞頻統計表（一般 - 搜尋模式，前 50 名）：
  詞語  頻率
  獲利  18
  營收  14
  下滑   6
  公司   6
  財務   5
  波動   5
  規模   5
  表現   5
  成長   4
  收成   4
 收波動   4
  台塑   4
  能力   4
  南亞   3
  其他   3
  優異   3
  大成   3
  普通   3
  分統   3
 三芳亞   2
  聚台   2
 台苯國   2
  低迷   2
 喬聯成   2
  達化   2
  根據   2
  無法   2
  粗略   2
  聯成   2
  石化   2
  穩定   2
  判斷   2
  中石   2
 達新上   2
 中石化   2
  持續   2
 穩健性   2
  只能   2
  轉虧   2
  虧損   2
  劇烈   2
台聚華夏   1
  定性   1
 大部分   1
 計算營   1
  我會   1
  大部   1
  近年   1
  趨勢   1
 粗略地   1
內容詞頻（搜尋模式）已儲存至 'word_freq_一般_搜尋模式.csv'



=== 表現等級：較差 ===

公司詞頻統計表（較差，前 50 名）：
   詞語  頻率
   統一   9
   台塑   7
   巨大   6
   南亞   6
   聯華   6
   福懋   5
   聯成   5
   大成   5
   京城   4
   長榮   4
   大洋   4
   東陽   4
  大統益   4
   三商   4
   卜蜂   4
   華電   3
  長榮航   3
   上曜   3
   華新   3
日月光投控   3
   達新   3
  中石化   3
   味全   3
   國喬   3
   台苯   3
  台達化   3
   亞聚   3
   三芳   3
   華夏   3
   勤誠   3
   亞泥   3
   佳格   3
  福懋油   3
  聯華食   3
  京城銀   3
   中華   3
   櫻花   3
   富采   3
   遠雄   3
  台積電   3
   台聚   3
   緯穎   2
   中化   2
   帝寶   2
   鼎基   2
  威強電   2
   健鼎   2
   鑽全   2
   台南   2
   憶聲   2
公司詞頻已儲存至 'company_freq_較差.csv'



內容詞頻統計表（較差 - 精確模式，前 50 名）：
  詞語  頻率
  獲利 596
  營收 412
  下滑 385
 收波動 126
  成長 107
  收成  97
  尚可  81
  波動  68
  持續  62
獲利波動  61
  轉虧  61
  穩定  51
  財務  48
 財務極  46
 獲利轉  41
  虧損  40
  金融  40
  不足  38
  穩健  37
  劇烈  34
 獲利平  33
  低迷  29
  數據  29
獲利持續  27
 獲利低  24
 獲利佳  19
  能力  18
 收平穩  18
 電營收  18
 業營收  17
  偏低  15
  主要  15
  建業  14
  轉負  14
  不穩  13
  近期  13
  休閒  12
 獲利強  12
  生活  11
  公司  11
  運動  11
 建業營  11
  居家  11
  槓桿  10
 環保營  10
 營建業   9
  表現   9
  平穩   9
  收回   9
  改善   9
內容詞頻（精確模式）已儲存至 'word_freq_較差_精確模式.csv'



內容詞頻統計表（較差 - 全模式，前 50 名）：
 詞語  頻率
 下滑 385
 收下 114
 收成  97
 尚可  81
 金融  41
 不足  38
 低迷  29
 能力  18
 回升  17
 主要  15
 偏低  15
 近期  13
 金金  13
 下市  13
 公司  12
 居家  11
 生活  11
 改善   9
 收回   9
 大幅   9
 衰退   8
 台塑   7
 近年   6
 巨大   6
 第一   6
 比率   5
 大成   5
 滑力   5
 其他   5
 小幅   4
 京城   4
 大洋   4
 中石   3
中石化   3
 石化   3
分公司   3
 一台   3
 月光   3
 新光   3
 不同   3
 日月   3
 可能   3
 佳景   3
 考量   3
 上市   3
 成大   3
 通分   3
 普通   3
 保金   3
 回落   3
內容詞頻（全模式）已儲存至 'word_freq_較差_全模式.csv'



內容詞頻統計表（較差 - 搜尋模式，前 50 名）：
  詞語  頻率
  獲利 596
  營收 412
  下滑 385
 收波動 126
  成長 107
  收成  97
  尚可  81
  波動  68
  持續  62
  轉虧  61
獲利波動  61
  穩定  51
  財務  48
 財務極  46
  金融  41
 獲利轉  41
  虧損  40
  不足  38
  穩健  37
  劇烈  34
 獲利平  33
  數據  29
  低迷  29
獲利持續  27
 獲利低  24
 獲利佳  19
  能力  18
 收平穩  18
 電營收  18
 業營收  17
  主要  15
  偏低  15
  轉負  14
  建業  14
  不穩  13
  近期  13
 獲利強  12
  公司  12
  休閒  12
  生活  11
 建業營  11
  運動  11
  居家  11
 環保營  10
  槓桿  10
  趨緩   9
  規模   9
  大幅   9
  改善   9
  平穩   9
內容詞頻（搜尋模式）已儲存至 'word_freq_較差_搜尋模式.csv'
